# Time-optimal (bang-bang) control for a double integrator 

An implementation of the time-optimal (or bang-bang) feedback control scheme is below

In [1]:
function control(x,umin,umax)
    y = x[1]                    # position
    v = x[2]                    # velocity
    s = y+1/2*v*abs(v)          # switching curve
    if s > 0                    # if above the curve
        u = umin
    elseif s < 0                # if below the curve
        u = umax
    elseif s == 0 && v > 0      # if on the switching curve on the left
        u = umin
    elseif s == 0 && v < 0      # if on the switching curve on the right
        u = umax
    else u = 0                  # if at (0,0)
    end
    return u
end

control (generic function with 1 method)

A state equation with the feedback control already plugged in is

In [2]:
A = [0 1; 0 0]
B = [0, 1]
f(x,p,t) = A*x + B*control(x,umin,umax)

f (generic function with 1 method)

Lower and upper bounds on the control signal are

In [3]:
umin = -1.0
umax = 1.0

1.0

The length of the time on which the simulation is to be performed is

In [4]:
tfinal = 3.6
tspan = (0.0,tfinal)

(0.0, 3.6)

The initial state is

In [5]:
x0 = [1.0,1.0]

2-element Array{Float64,1}:
 1.0
 1.0

Simulation follows

In [6]:
using DifferentialEquations

In [7]:
prob = ODEProblem(f,x0,tspan)
sol = solve(prob, Tsit5(), reltol=1e-8, abstol=1e-8)

retcode: Success
Interpolation: specialized 4th order "free" interpolation
t: 362900-element Array{Float64,1}:
 0.0
 0.011486983549970353
 0.12635681904967389
 1.275055174046709
 1.7400441392373673
 2.112035311389894
 2.1715538989342984
 2.1958023872920807
 2.2055017826351935
 2.209381540772439
 2.2186433666790046
 2.222760706208557
 2.223425915336137
 ⋮
 3.599993046571389
 3.599995116896062
 3.5999960939152316
 3.599996902357345
 3.5999975622861378
 3.599997848025323
 3.599998030131836
 3.5999990854488457
 3.59999954605054
 3.599999858763257
 3.5999999953916944
 3.6
u: 362900-element Array{Array{Float64,1},1}:
 [1.0, 1.0]
 [1.0114210081544317, 0.9885130164500296]
 [1.1183737961894977, 0.8736431809503261]
 [1.4621723256150707, -0.275055174046709]
 [1.226167335990216, -0.7400441392373671]
 [0.8816887331109957, -1.1120353113898935]
 [0.8137307309459271, -1.1715538989342977]
 [0.7850283252732854, -1.1958023872920802]
 [0.7733827260316902, -1.2055017826351933]
 [0.768698144419446, -1.20938

In [8]:
uopt = control.(sol.u,umin,umax)          # remember that DifferentialEquations labels the states as u

362900-element Array{Float64,1}:
 -1.0
 -1.0
 -1.0
 -1.0
 -1.0
 -1.0
 -1.0
 -1.0
 -1.0
 -1.0
 -1.0
 -1.0
 -1.0
  ⋮
 -1.0
  1.0
 -1.0
 -1.0
 -1.0
  1.0
  1.0
 -1.0
 -1.0
 -1.0
 -1.0
 -1.0

Finally, let's plot the simulation outcomes

In [9]:
using Plots

In [10]:
p1 = plot(sol,linewidth=3,title="Time-optimal regulation of a double integrator",
     xaxis="",yaxis="States",label=["v" "v"]) # legend=false
p2 = plot(sol.t,uopt,linewidth=3,xaxis="Time",yaxis="Control",label="u")
plot(p1,p2,layout=(2,1))

What we observe around the time 3.4 or so when the  system is near the origin, is an instance of the problem of *chattering*, that is, very fast switching of the controller between the two extreme values. Obviously, once reaching the origin, we expect the system stop switching and just set the control to zero (in other words, stop aplying any control whatsoever). How would you modify the code?